# Linear Solver Performance: XDG Poisson, Single Core

### Part 1, Benchmark Setup and Execution

In [ ]:
Console.WriteLine("Execution Date/time is " + DateTime.Now);

Execution Date/time is 06.11.2021 07:46:49


In [ ]:
#r "BoSSSpad.dll"
using System;
using System.Collections.Generic;
using System.Linq;
using ilPSP;
using ilPSP.Utils;
using BoSSS.Platform;
using BoSSS.Platform.LinAlg;
using BoSSS.Foundation;
using BoSSS.Foundation.XDG;
using BoSSS.Foundation.Grid;
using BoSSS.Foundation.Grid.Classic;
using BoSSS.Foundation.Grid.RefElements;
using BoSSS.Foundation.IO;
using BoSSS.Solution;
using BoSSS.Solution.Control;
using BoSSS.Solution.GridImport;
using BoSSS.Solution.Statistic;
using BoSSS.Solution.Utils;
using BoSSS.Solution.AdvancedSolvers;
using BoSSS.Solution.Gnuplot;
using BoSSS.Application.BoSSSpad;
using BoSSS.Application.XNSE_Solver;
using BoSSS.Application.XNSFE_Solver;
using static BoSSS.Application.BoSSSpad.BoSSSshell;
Init();


Error: System.MissingMethodException: Method not found: 'Void Microsoft.DotNet.Interactive.Formatting.Formatter.SetPreferredMimeTypeFor(System.Type, System.String)'.
   at BoSSS.Application.BoSSSpad.BoSSSshell.AddObjectFormatter[T](Func`2 optValFormatter)
   at BoSSS.Application.BoSSSpad.BoSSSshell.Init() in C:\Users\flori\Documents\BoSSS-NET5\public\src\L4-application\BoSSSpad\BoSSSshell.cs:line 99
   at Submission#4.<<Initialize>>d__0.MoveNext()
--- End of stack trace from previous location ---
   at Microsoft.CodeAnalysis.Scripting.ScriptExecutionState.RunSubmissionsAsync[TResult](ImmutableArray`1 precedingExecutors, Func`2 currentExecutor, StrongBox`1 exceptionHolderOpt, Func`2 catchExceptionOpt, CancellationToken cancellationToken)

In [ ]:
using BoSSS.Application.XdgPoisson3;

In [ ]:
ExecutionQueues

index type DeploymentBaseDirectory DeployRuntime Name DotnetRuntime BatchInstructionDir AllowedDatabasesPaths Username ServerName ComputeNodes DefaultJobPriority SingleNode Password PrivateKeyFilePath AdditionalBatchCommands DeploymentBaseDirectoryAtRemote SlurmAccount Email MonoDebug 0 BoSSS.Application.BoSSSpad.MiniBatchProcessorClient C:\Users\flori\AppData\Local\BoSSS-LocalJobs False LocalPC dotnet <null> [ { C:\BoSSS-Databases == : LocalMountPath: C:\BoSSS-Databases, PathAtRemote: }, { C:\Users\flori == : LocalMountPath: C:\Users\flori, PathAtRemote: } ] 1 BoSSS.Application.BoSSSpad.MsHPC2012Client \\dc1\userspace\kummer\cluster False FDY-WindowsHPC dotnet [ { \\dc1\userspace\kummer == : LocalMountPath: \\dc1\userspace\kummer, PathAtRemote: } ] FDY\kummer DC2 <null> Normal True 2 BoSSS.Application.BoSSSpad.SlurmClient W:\bosss_deploy False LbI dotnet fk69umer lcluster8.hrz.tu-darmstadt.de <null> C:\Users\flori\.ssh\id_rsa <null> /home/fk69umer/bosss_deploy project01287 <null> False 3 BoSSS.Application.BoSSSpad.SlurmClient X:\bosss_deploy False Lb2-specialPrj dotnet [ { X: == /work/scratch/fk69umer: LocalMountPath: X:, PathAtRemote: /work/scratch/fk69umer } ] fk69umer lcluster16.hrz.tu-darmstadt.de <null> C:\Users\flori\.ssh\id_rsa [ #SBATCH -p test24, #SBATCH -C avx512, #SBATCH --mem-per-cpu=8000 ] /work/scratch/fk69umer/bosss_deploy special00006 <null> False

In [ ]:
var myBatch = GetDefaultQueue();
myBatch

DeploymentBaseDirectory DeployRuntime Name DotnetRuntime BatchInstructionDir AllowedDatabasesPaths C:\Users\flori\AppData\Local\BoSSS-LocalJobs False LocalPC dotnet <null> [ { C:\BoSSS-Databases == : LocalMountPath: C:\BoSSS-Databases, PathAtRemote: }, { C:\Users\flori == : LocalMountPath: C:\Users\flori, PathAtRemote: } ]

In [ ]:
wmg.Init("LinslvPerf_XdgPoissonSer");
wmg.AllJobs

Project name is set to 'LinslvPerf_XdgPoissonSer'.
Creating database 'C:\BoSSS-Databases\LinslvPerf_XdgPoissonSer'.


(empty)

## Utility definitions

In [1]:
static class Utils {
    // DOF per cell in 3D
    public static int Np(int p) {
        return (p*p*p + 6*p*p + 11*p + 6)/6;
    }    
    
    //Non-equidistant nodes
    public static double[] SinLinSpacing(double l, double r, double a, int n) {
        double[] linnodes = GenericBlas.Linspace(-Math.PI * 0.5, Math.PI * 0.5, n);
        double[] linnodes2 = GenericBlas.Linspace(-1, 1, n);
        double[] nodes = new double[n];

        for (int i = 0; i < n; i++)
            //nodes[i] = linnodes2[i] * (1 - a) + (1.0 - Math.Sin(linnodes[i])) * a;
            nodes[i] = linnodes2[i] * (1 - a) + Math.Sin(linnodes[i])*a;

        for (int i = 0; i < n; i++)
            nodes[i] = nodes[i] * (r - l)*0.5 + l;
        return nodes;
    }
}

## Init grids and save to database

In [ ]:
wmg.Grids

IOException caught during creation/opening of database: The network path was not found. : '\\dc1\userspace\kummer\LinslvPerf_XdgPoissonSer'.
DirectoryNotFoundException caught during creation/opening of database: Could not find a part of the path 'X:\LinslvPerf_XdgPoissonSer'..


(empty)

Create meshes in various resolutions:
- domain $\Omega = (-1,1)^3$; 
- a Dirichlet boundary is set everywhere; the challenge of this benchmark,
  from a numerical point, is the 1:1000 ratio in the diffusion coefficient

In [ ]:
int[] Resolutions_3D = new int[] { 2 , 4, 8, 16, 32, 64 };
//int[] Resolutions_3D = new int[] { 2 };
IGridInfo[] grids = new IGridInfo[Resolutions_3D.Length];
for(int cnt = 0; cnt < Resolutions_3D.Length; cnt++) {
    int Res = Resolutions_3D[cnt];    
    
    double[] xNodes = GenericBlas.Linspace(-1, +1, Res + 1);
    double[] yNodes = GenericBlas.Linspace(-1, +1, Res + 1);
    double[] zNodes = GenericBlas.Linspace(-1, +1, Res + 1);
    int J = (xNodes.Length - 1)*(yNodes.Length - 1)*(zNodes.Length - 1);
    
    string GridName = string.Format(wmg.CurrentProject + "_J" + J);
    
    grids[cnt] = wmg.Grids.SingleOrDefault(grd => grd.Name.Contains(string.Format("_J"+ J))); // check if an appropriate grid is already present in the database
    if(grids[cnt] == null){
        Console.WriteLine("Creating grid with " + J + " cells.");
        
        GridCommons g;
        g      = Grid3D.Cartesian3DGrid(xNodes, yNodes, zNodes);
        g.Name = GridName;
        
        g.DefineEdgeTags(delegate (double[] X) {
            return "Dirichlet";
        });
      
        g = wmg.SaveGrid(g);  
        grids[cnt] = g;
    } else {
        Console.WriteLine("Found Grid: " + grids[cnt]);
        if(grids[cnt].NumberOfCells != J)
            throw new Exception("J mismatch");
        
        if(grids[cnt].SpatialDimension != 3)
            throw new Exception("D mismatch");
    }
}

Creating grid with 8 cells.
Grid Edge Tags changed.
Creating grid with 64 cells.
Grid Edge Tags changed.
Creating grid with 512 cells.
Grid Edge Tags changed.
Creating grid with 4096 cells.
Grid Edge Tags changed.
Creating grid with 32768 cells.
Grid Edge Tags changed.
Creating grid with 262144 cells.
Grid Edge Tags changed.


In [ ]:
grids

index EdgeTagNames PredefinedGridPartitioning Description StorageGuid BcCellsStorageGuid PeriodicTrafo InversePeriodicTrafo NoOfUpdateCells NoOfBcCells NumberOfCells_l NumberOfBcCells RefElements EdgeRefElements SpatialDimension CellPartitioning BcCellPartitioning MyRank Size NodePartitioning iGridData .. 0 [ { [0, inner edge]: Key: 0, Value: inner edge }, { [1, Dirichlet]: Key: 1, Value: Dirichlet } ] [ ] <null> bbc188d3-e9f9-419a-a3af-17e571f1742f 00000000-0000-0000-0000-000000000000 8 0 8 0 [ { BoSSS.Foundation.Grid.RefElements.Cube: HighestKnownOrder: 119, Volume: 8, HighestSupportedPolynomialDegree: 15, NoOfFaces: 6, Center: { 0 0 0
: Reference: 303, RefElement: { BoSSS.Foundation.Grid.RefElements.Cube: HighestKnownOrder: 119, Volume: 8, HighestSupportedPolynomialDegree: 15, NoOfFaces: 6, Center: { 0 0 0
: Reference: 303, RefElement: { BoSSS.Foundation.Grid.RefElements.Cube: HighestKnownOrder: 119, Volume: 8, HighestSupportedPolynomialDegree: 15, NoOfFaces: 6, Center: 0 0 0
, NoOfVertices: 8, FaceRefElement: BoSSS.Foundation.Grid.RefElements.Square, FaceTrafoGramianSqrt: [ 1, 1, 1, 1, 1, 1 ], VertexIndicesToFaces: [ [ 0, 3, 5 ], [ 1, 3, 5 ], [ 0, 2, 5 ], [ 0, 3, 4 ], [ 1, 2, 5 ], [ 1, 2, 4 ], [ 1, 3, 4 ], [ 0, 2, 4 ] ], VertexIndicesToCoFaces: [ [ 0, 3 ], [ 4 ], [ 0, 2 ], [ 1, 3 ], [ 4 ], [ 5 ], [ 5 ], [ 1, 2 ] ], FaceToVertexIndices: [ 0, 3, 2, 7, 1, 6, 4, 5, 2, 4, 7, 5, 0, 1, 3, 6, 3, 6, 7, 5 ... (4 more) ], FaceCenters: -1 0 0
1 0 0
0 1 0
0 -1 0
0 0 1
0 0 -1
, FaceNormals: -1 0 0
1 0 0
0 1 0
0 -1 0
0 0 1
0 0 -1
, SpatialDimension: 3, Vertices: -1 -1 -1
1 -1 -1
-1 1 -1
-1 -1 1
1 1 -1
1 1 1
1 -1 1
-1 1 1
, SubdivisonVertices: [ -1 0 -1
-1 -1 0
-1 -1 -1
0 -1 -1
-1 0 -1
-1 -1 0
-1 -1 0
0 -1 0
, 0 0 -1
0 -1 0
0 -1 -1
1 -1 -1
0 0 -1
0 -1 0
0 -1 0
1 -1 0
, -1 1 -1
-1 0 0
-1 0 -1
0 0 -1
-1 1 -1
-1 0 0
-1 0 0
0 0 0
, -1 0 0
-1 -1 1
-1 -1 0
0 -1 0
-1 0 0
-1 -1 1
-1 -1 1
0 -1 1
, 0 1 -1
0 0 0
0 0 -1
1 0 -1
0 1 -1
0 0 0
0 0 0
1 0 0
, 0 1 0
0 0 1
0 0 0
1 0 0
0 1 0
0 0 1
0 0 1
1 0 1
, 0 0 0
0 -1 1
0 -1 0
1 -1 0
0 0 0
0 -1 1
0 -1 1
1 -1 1
, -1 1 0
-1 0 1
-1 0 0
0 0 0
-1 1 0
-1 0 1
-1 0 1
0 0 1
 ], SupportedCellTypes: [ Cube_Linear, Cube_8, Cube_20, Cube_27, Cube_64, Cube_125, Cube_216 ], CoFaceVerticeIndices: [ 0, 2, 3, 7, 2, 7, 0, 3, 1, 4, 5, 6, 4, 5, 1, 6, 5, 7, 2, 4 ... (4 more) ], CoFace_FaceIndices: [ 0, 5, 0, 4, 0, 2, 0, 3, 1, 5, 1, 4, 1, 2, 1, 3, 2, 4, 2, 5 ... (4 more) ], NoOfCoFaces: 12 }, NoOfNodes: 1, SpatialDimension: 3, Dimension: 2, Lengths: [ 1, 3 ], Storage: [ 0, 0, 0 ], IsContinious: True, Length: 3, NoOfCols: 3, NoOfRows: 1, IsLocked: True }, NoOfVertices: 8, FaceRefElement: { BoSSS.Foundation.Grid.RefElements.Square: Volume: 4, HighestSupportedPolynomialDegree: 23, NoOfFaces: 4, Center: { 0 0
: Reference: 252, RefElement: BoSSS.Foundation.Grid.RefElements.Square, NoOfNodes: 1, SpatialDimension: 2, Dimension: 2, Lengths: [ 1, 2 ], Storage: [ 0, 0 ], IsContinious: True, Length: 2, NoOfCols: 2, NoOfRows: 1, IsLocked: True }, NoOfVertices: 4, FaceRefElement: { BoSSS.Foundation.Grid.RefElements.Line: FaceTrafoGramianSqrt: [ 1, 1 ], Volume: 2, HighestSupportedPolynomialDegree: 20, NoOfFaces: 2, Center: 0
, NoOfVertices: 2, FaceRefElement: BoSSS.Foundation.Grid.RefElements.Point, VertexIndicesToFaces: [ [ 0 ], [ 1 ] ], VertexIndicesToCoFaces: [ <null>, <null> ], FaceToVertexIndices: [ 0, 1 ], FaceCenters: -1
1
, FaceNormals: -1
1
, SpatialDimension: 1, Vertices: -1
1
, HighestKnownOrder: 119, SubdivisonVertices: [ -1
0
, 0
1
 ], SupportedCellTypes: [ Line_2, Line_3, Line_4, Line_5, Line_6 ], CoFaceVerticeIndices: [ ], CoFace_FaceIndices: [ ], NoOfCoFaces: 0 }, FaceTrafoGramianSqrt: [ 1, 1, 1, 1 ], VertexIndicesToFaces: [ [ 0, 3 ], [ 1, 3 ], [ 0, 2 ], [ 1, 2 ] ], VertexIndicesToCoFaces: { System.IndexOutOfRangeException: Index was outside the bounds of the array.
 at BoSSS.Foundation.Grid.RefElements.RefElement.get_VertexInd

## Setup Control Object for a Solver Run

### Values/Formulas for the Values of RHS and Boundary Conditions

In [1]:
static class InitialValues {
    public static double RHS(double[] X) {
        return -Math.Sin(X[0]);
    }
    
    public static double DirichletBC(double[] X) {
        return 0.0;
    }
    
    public static double NeumannBC(double[] X) {
       if(Math.Abs(X[1] - 1.0) < 1.0e-8 || Math.Abs(X[1] + 1.0) < 1.0e-8)
           return 0;
       if(X.Length > 2 && (Math.Abs(X[2] - 1.0) < 1.0e-8 || Math.Abs(X[2] + 1.0) < 1.0e-8))
           return 0;

       return Math.Cos(10.0);
   }
}

In [1]:
//InitialValues.RHS(new double[]{ 1,1});

In [1]:
// - - - - - - - - - - - - -
// setup of parameter study
// - - - - - - - - - - - - -

In [1]:
List<XdgPoisson3Control> controls = new List<XdgPoisson3Control>();

In [1]:
// polynomial degrees to test
//int[] PolyDegS = new int[] {2, 3, 4, 5, 6};
int[] PolyDegS = new int[] {2, 3 ,5};
//int[] PolyDegS = new int[] {3};

In [1]:
// Solvers which we want to instrument:
LinearSolverConfig.Code[] solver_nameS = new LinearSolverConfig.Code[] {
    //LinearSolverConfig.Code.classic_pardiso, 
    LinearSolverConfig.Code.classic_mumps, 
    //LinearSolverConfig.Code.classic_cg,
    LinearSolverConfig.Code.exp_softpcg_schwarz_directcoarse,
    LinearSolverConfig.Code.exp_softpcg_mg
}; 

In [1]:
// MaxDof for one claculation (we skip fine grids for higher polynomial orders)
int MaxDof = 5000000;

In [1]:
using BoSSS.Solution.XNSECommon;
using BoSSS.Foundation.XDG;

In [1]:
controls.Clear();
foreach(LinearSolverConfig.Code solver_name in solver_nameS) {
foreach(int k in PolyDegS) {
int iGrd = 0;    
foreach(IGridInfo grd in grids) {
    iGrd ++;
    //if(k >= 3 && iGrd > 6)
    //    continue; 
    //if(k >= 4 && iGrd > 5)
    //    continue; 
    //if(k >= 5 && iGrd > 4)
    //    continue; 
    
    int Np = Utils.Np(k);
    int J  = grd.NumberOfCells;
    if(J*Np > MaxDof)
        continue;
    
    string caseName = string.Format("J{0}_k{1}_{2}", J, k, solver_name);
    Console.WriteLine("setting up: " + caseName);

    var ctrl = new XdgPoisson3Control();
    
    
    //ctrl.SessionName = caseName;
    
    ctrl.savetodb = true; //for debug's sake
    ctrl.SetDatabase(tempDB);
    ctrl.SetGrid(grd);
    //ctrl.SetDGdegree(k);
    
    ctrl.FieldOptions.Add("Phi", new FieldOpts() {
         Degree = 2,
         SaveToDB = FieldOpts.SaveToDBOpt.TRUE
    });
    ctrl.FieldOptions.Add("u", new FieldOpts() {
         Degree = k,
         SaveToDB = FieldOpts.SaveToDBOpt.TRUE
    });

    ctrl.SuppressExceptionPrompt           = true;
    ctrl.LinearSolver.SolverCode           = solver_name;
    ctrl.LinearSolver.NoOfMultigridLevels  = 10;
    ctrl.LinearSolver.ConvergenceCriterion = 1e-6;
    
    double radius           = 0.7;
    ctrl.ExcactSolSupported = false;
    ctrl.InitialValues.Add("Phi", new Formula("X => X[0].Pow2()+X[1].Pow2()+X[2].Pow2()-"+radius+".Pow2()"));
    ctrl.MU_A = -1;
    ctrl.MU_B = -1000;
    ctrl.InitialValues.Add("rhs#A", new Formula("X => 1"));
    ctrl.InitialValues.Add("rhs#B", new Formula("X => 1"));
    ctrl.InitialValues.Add("u#A", new Formula ("X => 0"));
    ctrl.InitialValues.Add("u#B", new Formula ("X => 0"));
    //ctrl.AddBoundaryValue("Dirichlet", "u#A",
    //    GetFormulaObject(InitialValues.DirichletBC));
    //ctrl.AddBoundaryValue("Dirichlet", "u#B",
    //    GetFormulaObject(InitialValues.DirichletBC));
    //ctrl.AddBoundaryValue("Neumann", "u#A",
    //    GetFormulaObject(InitialValues.NeumannBC));
    //ctrl.AddBoundaryValue("Neumann", "u#B",
    //    GetFormulaObject(InitialValues.NeumannBC));
    ctrl.CutCellQuadratureType = XQuadFactoryHelper.MomentFittingVariants.Classic;
    ctrl.SetDefaultDiriBndCnd  = true;
    ctrl.ViscosityMode         = XLaplace_Interface.Mode.SIP;
    ctrl.SessionName           = "XdgPoissonVelocity_"+caseName;
    ctrl.ProjectName           = WFlowName;
    
    ctrl.AgglomerationThreshold = 0.1;
    
    controls.Add(ctrl);
}
}
}

In [1]:
// ==========
// Launch Job
// ==========

In [1]:
//var solver = new XdgPoisson3Main();
//solver.Init(controls[0]);
//solver.RunSolverMode();
//solver.Dispose();

In [1]:
//WorkflowMgm.AllJobs.Pick(0);
//WorkflowMgm.AllJobs.Pick(0).Value.Stdout;
//WorkflowMgm.AllJobs.Pick(0).Value.Stderr;

In [1]:
//tempDB.Sessions.Where(s => s.Name.Contains("softpcg") && s.Name.Contains("k2") && s.Name.Contains("mg"));//.ForEach(si => si.Delete(true));
//tempDB.Sessions.Where(s => s.Name.Contains("exp_direct")).ForEach(si => si.Delete());

In [1]:
foreach(var ctrl in controls) {
    Console.WriteLine(" Submitting: " + ctrl.SessionName); 
    ctrl.RunBatch(myBatch);
}

In [1]:
WorkflowMgm.AllJobs;

In [1]:
//write out stout
Dictionary<string, string> Stoutlist = new Dictionary<string, string>();
//var somelist = WorkflowMgm.AllJobs.Where(s=>s.Value.Status.Equals(JobStatus.Failed));
var somelist = WorkflowMgm.AllJobs;
somelist.ForEach(j=>Stoutlist.Add(j.Value.Name ,j.Value.Stdout.ToString()));
foreach(KeyValuePair<string,string> stout in Stoutlist){
    using(StreamWriter sw = new StreamWriter("Stout_"+stout.Key+".txt")){
    Console.Write("writing {0} ...",stout.Key);
    sw.WriteLine(stout.Value);
    Console.WriteLine("done.");
    }
}

In [1]:
tempDB.Projects.Where(p=>p.Key.Contains(WFlowName)).Pick(0).Value;

In [1]:
tempDB.Projects.Where(p=>p.Key.Contains(WFlowName)).Pick(0).Value.RunningOrCrashed().ForEach(s=>Console.WriteLine(s.Name));

In [1]:
tempDB.Projects.Where(p=>p.Key.Contains(WFlowName)).Pick(0).Value.RunningOrCrashed();
//tempDB.Projects.Where(p=>p.Key.Contains(WFlowName)).Pick(0).Value.RunningOrCrashed().DeleteAll();
//WorkflowMgm.AllJobs.Select(kv => kv.Key + ": \t" + kv.Value.Status);
WorkflowMgm.AllJobs.Where(s => s.Value.Status.Equals(JobStatus.InProgress)).Pick(0).Value.Stdout;
WorkflowMgm.AllJobs.Pick(0).Value.Stdout;

In [1]:
//WorkflowMgm.AllJobs.ElementAt(9).Value.Stdout;

In [1]:
//WorkflowMgm.AllJobs.ElementAt(0).Value.Stdout;

In [1]:
WorkflowMgm.SessionTable.Rows.Count;

In [1]:
//tempDB.Projects.Where(p=>p.Key.Contains(WFlowName)).Pick(0).Value.Pick(4);
//tempDB.Projects.Where(p=>p.Key.Contains(WFlowName)).Pick(0).Value.Pick(4).OpenSessionDirectory();

In [1]:
tempDB.Projects.Where(p=>p.Key.Contains(WFlowName)).Pick(0).Value.Pick(4).Timesteps.Last().Fields.Pick(1).Coordinates.NoOfCols;

In [1]:
// =====================================
// Session table
// =====================================

In [1]:
// -------------------------------
// Additional/user-defined columns
// -------------------------------
tempDB.Projects.Pick(0).Value.Pick(0).KeysAndQueries;

In [1]:
static class AddCols {
    static public object SipMatrixAssembly_time(ISessionInfo SI) {
        var mcr = SI.GetProfiling()[0];
        var ndS = mcr.FindChildren("SipMatrixAssembly");
        var nd  = ndS.ElementAt(0);
        return nd.TimeSpentInMethod.TotalSeconds  / nd.CallCount;
    }
    static public object Aggregation_basis_init_time(ISessionInfo SI) {
        var mcr = SI.GetProfiling()[0];
        var ndS = mcr.FindChildren("Aggregation_basis_init");
        var nd  = ndS.ElementAt(0);
        return nd.TimeSpentInMethod.TotalSeconds  / nd.CallCount;
    }
    static public object Solver_Init_time(ISessionInfo SI) {
        var mcr = SI.GetProfiling()[0];
        var ndS = mcr.FindChildren("Solver_Init");
        var nd  = ndS.ElementAt(0);
        //Console.WriteLine("Number of nodes: " + ndS.Count() + " cc " + nd.CallCount );
        return nd.TimeSpentInMethod.TotalSeconds / nd.CallCount;
    }
    static public object Solver_Run_time(ISessionInfo SI) {
        var mcr = SI.GetProfiling()[0];
        var ndS = mcr.FindChildren("Solver_Run");
        var nd  = ndS.ElementAt(0);
        return nd.TimeSpentInMethod.TotalSeconds  / nd.CallCount;
    }
}

In [1]:
WorkflowMgm.AdditionalSessionTableColums.Clear();
WorkflowMgm.AdditionalSessionTableColums.Add(
    "SipMatrixAssembly_time", AddCols.SipMatrixAssembly_time);
WorkflowMgm.AdditionalSessionTableColums.Add(
    "Aggregation_basis_init_time", AddCols.Aggregation_basis_init_time);
WorkflowMgm.AdditionalSessionTableColums.Add(
    "Solver_Init_time", AddCols.Solver_Init_time);
WorkflowMgm.AdditionalSessionTableColums.Add(
    "Solver_Run_time", AddCols.Solver_Run_time);

In [1]:
// --------------------------
// Save Session table in file
// --------------------------

In [1]:
var SessTab = WorkflowMgm.SessionTable;

In [1]:
SessTab.Rows.Count;

In [1]:
// The Session column can't be serialized,
// we have to remove it
List<string> AllCols = SessTab.GetColumnNames().ToList();
AllCols.Remove("Session");

In [1]:
SessTab = SessTab.ExtractColumns(AllCols.ToArray());

In [1]:
using System.IO;

In [1]:
// Filename
var now           = DateTime.Now;
SessTab.TableName = "SolverRuns--" + now.Year + "-" + now.Month + "-" + now.Day;
string docpath    = Path.Combine(CurrentDocDir, SessTab.TableName + ".json");

In [1]:
// save session table as file: this can be stored in our git 
// repository
SessTab.SaveToFile(docpath);

In [1]:
LastError;